<a href="https://colab.research.google.com/github/ladyada/notebooks/blob/master/Speech_Training.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Speech Recognition Training Notebook



In [2]:
import os.path
from google.colab import drive

DRIVE_STORAGE_PATH = '/content/drive/My Drive/speech-recognition'

def ensure_drive():
  if not os.path.exists('/content/drive/My Drive'):
    drive.mount('/content/drive', force_remount=True)
    
ensure_drive()

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


## Download TensorFlow

In [3]:
# Clone the repository from GitHub
!git clone -q https://github.com/tensorflow/tensorflow
# Check out a commit that has been tested to work
# with the build of TensorFlow we're using
!git -c advice.detachedHead=false -C tensorflow checkout 17ce384df70

Checking out files: 100% (8496/8496), done.
HEAD is now at 17ce384df7 Share ownership of `UnboundedWorkQueue` between collective executor and executor manager.


## Create trained model

In [0]:
!cd tensorflow && python3 tensorflow/examples/speech_commands/train.py --model_architecture=tiny_conv --window_stride=20 --preprocess=mfcc --wanted_words="yes,no" --silence_percentage=25 --unknown_percentage=25 --quantize=1

2019-10-21 17:50:17.104694: I tensorflow/core/platform/profile_utils/cpu_utils.cc:94] CPU Frequency: 2300000000 Hz
2019-10-21 17:50:17.104928: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x2f09100 initialized for platform Host (this does not guarantee that XLA will be used). Devices:
2019-10-21 17:50:17.104965: I tensorflow/compiler/xla/service/service.cc:176]   StreamExecutor device (0): Host, Default Version
2019-10-21 17:50:17.121121: I tensorflow/stream_executor/platform/default/dso_loader.cc:44] Successfully opened dynamic library libcuda.so.1
2019-10-21 17:50:17.191541: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:983] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2019-10-21 17:50:17.192433: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x2f092c0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2019-10-21 17:50:17

### Optional: Visualize graph and training rate

In [0]:
%load_ext tensorboard
%tensorboard --logdir /tmp/retrain_logs

In [0]:
!cp -vr /tmp/speech_commands_train "{DRIVE_STORAGE_PATH}/"

'/tmp/speech_commands_train' -> '/content/drive/My Drive/speech-recognition/speech_commands_train'
'/tmp/speech_commands_train/tiny_conv.ckpt-17600.meta' -> '/content/drive/My Drive/speech-recognition/speech_commands_train/tiny_conv.ckpt-17600.meta'
'/tmp/speech_commands_train/tiny_conv_labels.txt' -> '/content/drive/My Drive/speech-recognition/speech_commands_train/tiny_conv_labels.txt'
'/tmp/speech_commands_train/tiny_conv.ckpt-17700.meta' -> '/content/drive/My Drive/speech-recognition/speech_commands_train/tiny_conv.ckpt-17700.meta'
'/tmp/speech_commands_train/tiny_conv.ckpt-17800.meta' -> '/content/drive/My Drive/speech-recognition/speech_commands_train/tiny_conv.ckpt-17800.meta'
'/tmp/speech_commands_train/tiny_conv.ckpt-17900.meta' -> '/content/drive/My Drive/speech-recognition/speech_commands_train/tiny_conv.ckpt-17900.meta'
'/tmp/speech_commands_train/tiny_conv.ckpt-18000.meta' -> '/content/drive/My Drive/speech-recognition/speech_commands_train/tiny_conv.ckpt-18000.meta'
'/tmp

## Freeze Graph

In [0]:
!python tensorflow/tensorflow/examples/speech_commands/freeze.py --model_architecture=tiny_conv --window_stride=20 --preprocess=mfcc --wanted_words="yes,no" --quantize=1 --output_file="{DRIVE_STORAGE_PATH}/tiny_conv.pb" --start_checkpoint="{DRIVE_STORAGE_PATH}/speech_commands_train/tiny_conv.ckpt-18000"

2019-10-21 21:10:13.426128: I tensorflow/core/platform/profile_utils/cpu_utils.cc:94] CPU Frequency: 2300000000 Hz
2019-10-21 21:10:13.426386: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x25eb2c0 initialized for platform Host (this does not guarantee that XLA will be used). Devices:
2019-10-21 21:10:13.426423: I tensorflow/compiler/xla/service/service.cc:176]   StreamExecutor device (0): Host, Default Version
2019-10-21 21:10:13.442540: I tensorflow/stream_executor/platform/default/dso_loader.cc:44] Successfully opened dynamic library libcuda.so.1
2019-10-21 21:10:13.511223: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:983] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2019-10-21 21:10:13.512023: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x25eb480 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2019-10-21 21:10:13

## Convert to TFLite (may not be needed?)

In [0]:
!toco --graph_def_file="{DRIVE_STORAGE_PATH}/tiny_conv.pb" --output_file="{DRIVE_STORAGE_PATH}/tiny_conv.tflite" --input_shapes=1,49,40,1 --input_arrays=Reshape_1 --output_arrays='labels_softmax' --inference_type=QUANTIZED_UINT8 --mean_values=0 --std_dev_values=9.8077

2019-10-21 21:10:58.069629: I tensorflow/stream_executor/platform/default/dso_loader.cc:44] Successfully opened dynamic library libcuda.so.1
2019-10-21 21:10:58.101409: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:983] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2019-10-21 21:10:58.102185: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1618] Found device 0 with properties: 
name: Tesla K80 major: 3 minor: 7 memoryClockRate(GHz): 0.8235
pciBusID: 0000:00:04.0
2019-10-21 21:10:58.102478: I tensorflow/stream_executor/platform/default/dso_loader.cc:44] Successfully opened dynamic library libcudart.so.10.0
2019-10-21 21:10:58.103689: I tensorflow/stream_executor/platform/default/dso_loader.cc:44] Successfully opened dynamic library libcublas.so.10.0
2019-10-21 21:10:58.104799: I tensorflow/stream_executor/platform/default/dso_loader.cc:44] Successfully opened dynamic library libcufft.so.10.

## Spot checks

In [0]:
import os.path
if not os.path.exists('/tmp/speech_dataset'):
  !wget https://storage.googleapis.com/download.tensorflow.org/data/speech_commands_v0.02.tar.gz
  !mkdir /tmp/speech_dataset
  !tar -xzf speech_commands_v0.02.tar.gz -C /tmp/speech_dataset

ensure_drive()


for phrase in ('yes', 'no', 'right'):
  wav = !ls -1 /tmp/speech_dataset/{phrase}/*.wav | head -n 1
  wav = wav[0]

  print('')
  print(f'{phrase:10s} <' + '-' * 69)
  !cd tensorflow && python tensorflow/examples/speech_commands/label_wav.py --graph="{DRIVE_STORAGE_PATH}/tiny_conv.pb" --labels="{DRIVE_STORAGE_PATH}/speech_commands_train/tiny_conv_labels.txt" --wav={wav} 2>/dev/null



yes        <---------------------------------------------------------------------
yes (score = 0.97023)
_unknown_ (score = 0.02556)
no (score = 0.00415)

no         <---------------------------------------------------------------------
no (score = 0.49113)
yes (score = 0.36273)
_unknown_ (score = 0.14614)

right      <---------------------------------------------------------------------
_unknown_ (score = 0.84957)
no (score = 0.07522)
yes (score = 0.07522)
